In [26]:
import pandas as pd
import numpy as np
import torch
import math
import random
#import sklearn as skl

In [27]:
data = pd.read_csv("triplets_all.csv")
data

ids  intersize
0           0_0         46
1           0_1          5
2           0_2          2
3           0_3         14
4           0_4         10
...         ...        ...
385876  875_876          0
385877  875_877          0
385878  876_876         43
385879  876_877          3
385880  877_877         72

[385881 rows x 2 columns]

In [135]:
data.iloc[2, 0]

'0_2'

In [28]:
n, N = 878, 385881

In [29]:
sz = [0] * n
ist = [[0] * n for i in range(n)]
for i in range(N):
    s1, s2 = data.iloc[i, 0], data.iloc[i, 1]
    x1, x2 = map(int, s1.split('_'))
    sz = int(s2)
    if (x1 >=n or x2 >= n):
        break
    ist[x1][x2] = sz
    ist[x2][x1] = sz

In [30]:
J = [[0] * n for i in range(n)]
for i in range(n):
    for j in range(n):
        J[i][j] = ist[i][j]

In [31]:
J = torch.tensor(J)

In [32]:
J

tensor([[ 46,   5,   2,  ...,   0,   0,   0],
        [  5, 121,   8,  ...,   0,   0,   0],
        [  2,   8,  43,  ...,   0,   0,   0],
        ...,
        [  0,   0,   0,  ...,  40,   0,   0],
        [  0,   0,   0,  ...,   0,  43,   3],
        [  0,   0,   0,  ...,   0,   3,  72]])

In [130]:
u,e,v = np.linalg.svd(J)

In [135]:
D = np.multiply(u, e)

In [175]:
D

tensor([[-1.4164e+02,  5.3458e+00, -1.7858e+01,  ...,  1.0214e-01,
         -1.7124e-02,  3.9185e-02],
        [-3.1155e+02,  3.2432e+01,  3.8506e+01,  ...,  6.0150e-02,
         -4.2823e-02, -7.9223e-02],
        [-1.3596e+02,  2.4614e+01,  3.4995e+01,  ...,  2.2030e-01,
          3.7408e-02, -1.6091e-01],
        ...,
        [-1.1198e+02,  4.4172e+01, -3.9888e+01,  ...,  1.5161e-01,
          8.2942e-02,  8.4598e-02],
        [-2.3968e+01, -7.8147e+00, -1.8420e+01,  ...,  1.0101e-01,
          1.0956e-01, -1.1516e-01],
        [-1.5269e+02, -6.3643e+01,  1.5377e+01,  ..., -2.6042e-02,
         -6.1860e-02, -4.2380e-02]], dtype=torch.float64)

In [33]:
def kekloss(J, A, w):
    global D
    D = torch.tensor(D)
    D.requires_grad = True
    A = torch.tensor(A, dtype = torch.float64)
    A.requires_grad = True
    X = torch.matmul(D, A)
    X = (X - 1) * (X - 1)
    X = torch.tensor(X, dtype = torch.double)
    #X.requires_grad = True
    n, m = X.shape
    O = torch.zeros(n, m)
    O = torch.tensor(O, dtype = torch.double)
    O.requires_grad = True
    return torch.nn.MSELoss(reduction="sum")(X, O)

def myloss(J, A, w):
    n, m = A.shape
    B = torch.matmul(A, A.T)
    C = (J - B) * (J - B)
    O = torch.zeros(n, n)
    O.requires_grad = True
    reg = ((A - 1) * (A - 1)).sum()
    return torch.nn.L1Loss(reduction="sum")(C, O) + w * reg

def AE(J, A):
    J = torch.tensor(J)
    A = torch.tensor(A, dtype = torch.double)
    A_bin = (A>0.5).float()
    B = torch.matmul(A_bin, A_bin.T)
    C = (J - B)
    C = torch.abs(C)
    return C.sum() / (n * n)

def checkERROR(J, A):
    B = np.matmul(A, A.T)
    C = (J - B)
    C = np.abs(C)
    return C.sum()

In [230]:
m = 2000
A = torch.zeros(n, m)
for i in range(n):
    for j in range(m):
        A[i][j] = np.random.rand()
        A[i][j] %= 2

In [231]:
loss = 0

In [309]:
A = torch.tensor(A)
A.requires_grad = True
J = torch.tensor(J)

/var/folders/cc/61bdd5zn7mvd_2qfdfxfhj4m0000gn/T/ipykernel_14335/1266228094.py:1: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  A = torch.tensor(A)


In [313]:
A

tensor([[0.1163, 0.1166, 0.1140,  ..., 0.1191, 0.1199, 0.1138],
        [0.1118, 0.1116, 0.1159,  ..., 0.1141, 0.1131, 0.1140],
        [0.1162, 0.1161, 0.1166,  ..., 0.1191, 0.1170, 0.1146],
        ...,
        [0.1147, 0.1165, 0.1135,  ..., 0.1165, 0.6030, 0.1104],
        [0.1240, 0.1213, 0.5971,  ..., 0.1246, 0.1213, 0.1193],
        [0.1181, 0.1163, 0.1166,  ..., 0.1227, 0.1205, 0.1172]],
       dtype=torch.float64, requires_grad=True)

In [314]:
optimizer = torch.optim.Adam([A], lr = 0.1)
for i in range(3000):
    optimizer.zero_grad()
    loss = myloss(J, A, 10000)
    print(loss)
    loss.backward()
    optimizer.step()
    print(float(AE(J, A)))

tensor(1.4085e+10, dtype=torch.float64, grad_fn=<AddBackward0>)
3.2621679306030273
tensor(1.4824e+10, dtype=torch.float64, grad_fn=<AddBackward0>)


/var/folders/cc/61bdd5zn7mvd_2qfdfxfhj4m0000gn/T/ipykernel_14335/2735192503.py:27: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  J = torch.tensor(J)
/var/folders/cc/61bdd5zn7mvd_2qfdfxfhj4m0000gn/T/ipykernel_14335/2735192503.py:28: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  A = torch.tensor(A, dtype = torch.double)


6.556462287902832
tensor(1.4070e+10, dtype=torch.float64, grad_fn=<AddBackward0>)
6.5839009284973145
tensor(1.4238e+10, dtype=torch.float64, grad_fn=<AddBackward0>)
6.5893235206604
tensor(1.4241e+10, dtype=torch.float64, grad_fn=<AddBackward0>)
6.590045928955078
tensor(1.4178e+10, dtype=torch.float64, grad_fn=<AddBackward0>)
6.588542461395264
tensor(1.4059e+10, dtype=torch.float64, grad_fn=<AddBackward0>)
6.5789794921875
tensor(1.3964e+10, dtype=torch.float64, grad_fn=<AddBackward0>)
6.572916507720947
tensor(1.3955e+10, dtype=torch.float64, grad_fn=<AddBackward0>)
6.571779727935791
tensor(1.3966e+10, dtype=torch.float64, grad_fn=<AddBackward0>)
6.571559429168701
tensor(1.4010e+10, dtype=torch.float64, grad_fn=<AddBackward0>)
6.569621562957764
tensor(1.4041e+10, dtype=torch.float64, grad_fn=<AddBackward0>)
6.5651655197143555
tensor(1.3997e+10, dtype=torch.float64, grad_fn=<AddBackward0>)
6.558501720428467
tensor(1.3928e+10, dtype=torch.float64, grad_fn=<AddBackward0>)
6.554895401000977


KeyboardInterrupt: 

In [277]:
m = 2000
A = np.zeros((n, m))
J = np.array(J)
loss = 0
for i in range(n):
    for j in range(m):
        #A[i][j] = i + j + i * i
        #A[i][j] %= 2
        A[i][j] = 0
G = np.matmul(A, A.T)
loss = np.abs(G - J).sum()

In [278]:
loss

5080469.0

In [272]:
i, j

(877, 1999)

In [276]:
np.matmul(A, A.T).sum()

1.0

In [271]:
mulka(A, J, i, j, 1, loss, G)

5080469.0

In [280]:
def stupid(A, J, i, j, w):
    global n, m, G
    l1 = np.abs((G - J)).sum()
    A[i][j] += w
    G = np.matmul(A, A.T)
    l2 = np.abs((G - J)).sum()
    return l2 - l1

def mulka(A, J, i, j, w, loss, G):
    global n, m
    for k in range(n):
        loss -= abs(J[k][i] - G[k][i])
        if (i != k):
            loss -= abs(J[i][k] - G[i][k])
    for k in range(n):
        G[k][i] += w * A[k][j]
    for k in range(n):
        G[i][k] += w * A[k][j]
    G[i][i] += 1
    for k in range(n):
        loss += abs(J[k][i] - G[k][i])
        if (i != k):
            loss += abs(J[i][k] - G[i][k])
    A[i][j] += w
    return loss

In [281]:
loss

5080469.0

In [282]:
checkERROR(J, A), np.abs(G - J).sum()

(5080469.0, 5080469.0)

83520.0

In [302]:
# T0 = 100
T = T0
print(loss)
for t in range(1, 10000):
    #print(G.sum())
    i = random.randint(0, n - 1)
    j = random.randint(0, m - 1)
    
    if (A[i][j] == 1):
        loss_before = loss
        loss = mulka(A, J, i, j, -1, loss, G)
        #print(loss, checkERROR(J, A))
        dloss = loss - loss_before
        if (dloss >= 0):
            p = math.exp(-dloss / T)
            if (np.random.rand() >= p):
                loss = mulka(A, J, i, j, 1, loss, G)
    else:
        loss_before = loss
        loss = mulka(A, J, i, j, 1, loss, G)
        #print(loss, checkERROR(J, A))
        dloss = loss - loss_before
        if (dloss >= 0):
            p = math.exp(-dloss / T)
            if (np.random.rand() >= p):
                loss = mulka(A, J, i, j, -1, loss, G)
    T = T0 / t
    if (i % 100 == 0):
        print(loss)

2577196.0
2577126.0
2577126.0
2577090.0
2576743.0
2576728.0
2576728.0
2576449.0
2576392.0
2576175.0
2576175.0
2575955.0
2575588.0
2575552.0
2575552.0
2574863.0
2574631.0
2574606.0
2574553.0
2574393.0
2574259.0
2573988.0
2573988.0
2573880.0
2573880.0
2573229.0
2572552.0
2572355.0
2572193.0
2572131.0
2572130.0
2571747.0
2571731.0
2571731.0
2571731.0
2571496.0
2570878.0
2569477.0
2569312.0
2569198.0
2569198.0
2569198.0
2567779.0
2567507.0
2567462.0
2566812.0
2566616.0
2566592.0
2566592.0
2566235.0
2565878.0
2565255.0
2565174.0
2564707.0
2564577.0
2564266.0
2563953.0
2562942.0
2562694.0
2562694.0
2562585.0
2562493.0
2562366.0
2562323.0
2561968.0
2561968.0
2561968.0
2561833.0
2561247.0
2560836.0
2560812.0
2559370.0
2559097.0
2558846.0
2558712.0
2558627.0
2558597.0
2558126.0
2557816.0
2557816.0
2557560.0
2557454.0
2556307.0
2556176.0
2555993.0
2555778.0
2555446.0
2555164.0
2554554.0
2554510.0
2554464.0
2553950.0
2553886.0
2553852.0
2553325.0
2552961.0
2552791.0
2552791.0
2552481.0
2552369.0


In [299]:
loss

2932790.0

In [300]:
checkERROR(J, A)

2932790.0

In [210]:
checkERROR(J, A)

5079020.0

In [77]:
checkERROR(J, A)

764970794.0

In [75]:
loss

764969719.0

In [89]:
G = J

In [154]:
N = 878 * 2000
graph = [[] for _ in range(N)]

In [177]:
graph

[[1544000,
  1546000,
  1548000,
  1550000,
  1552000,
  1554000,
  1556000,
  1558000,
  1560000,
  1562000,
  1564000,
  1566000,
  1568000,
  1570000,
  1572000,
  1574000,
  1576000,
  1578000,
  1580000,
  1582000,
  1584000,
  1586000,
  1588000,
  1590000,
  1592000,
  1594000,
  1596000,
  1598000,
  1600000,
  1602000,
  1604000,
  1606000,
  1608000,
  1610000,
  1612000,
  1614000,
  1616000,
  1618000,
  1620000,
  1622000,
  1624000,
  1626000,
  1628000,
  1630000,
  1632000,
  1634000,
  1636000,
  1638000,
  1640000,
  1642000,
  1644000,
  1646000,
  1648000,
  1650000,
  1652000,
  1654000,
  1656000,
  1658000,
  1660000,
  1662000,
  1664000,
  1666000,
  1668000,
  1670000,
  1672000,
  1674000,
  1676000,
  1678000,
  1680000,
  1682000,
  1684000,
  1686000,
  1688000,
  1690000,
  1692000,
  1694000,
  1696000,
  1698000,
  1700000,
  1702000,
  1704000,
  1706000,
  1708000,
  1710000,
  1712000,
  1714000,
  1716000,
  1718000,
  1720000,
  1722000,
  1724000,

In [155]:
for i in range(878):
    for j in range(878):
        if (G[i][j] == 0):
            for k in range(m):
                graph[i * m + k].append(j * m + k)
                graph[j * m + k].append(i * m + k)

In [156]:
used = [0] * N

In [160]:
c = 0
def dfs(v):
    if (used[v]):
        return;
    used[v] = 1
    for u in graph[v]:
        dfs(u)

In [161]:
for i in range(N):
    if (used[i] == 0):
        c += 1
        if (c % 100 == 0):
            print(c)
        dfs(i)

100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
3000
3100
3200
3300
3400
3500
3600
3700
3800
3900
4000
4100
4200
4300
4400
4500
4600
4700
4800
4900
5000
5100
5200
5300
5400
5500
5600
5700
5800
5900
6000
6100
6200
6300
6400
6500
6600
6700
6800
6900
7000
7100
7200
7300
7400
7500
7600
7700
7800
7900
8000
8100
8200
8300
8400
8500
8600
8700
8800
8900
9000
9100
9200
9300
9400
9500
9600
9700
9800
9900
10000
10100
10200
10300
10400
10500
10600
10700
10800
10900
11000
11100
11200
11300
11400
11500
11600
11700
11800
11900
12000
12100
12200
12300
12400
12500
12600
12700
12800
12900
13000
13100
13200
13300
13400
13500
13600
13700
13800
13900
14000
14100
14200
14300
14400
14500
14600
14700
14800
14900
15000
15100
15200
15300
15400
15500
15600
15700
15800
15900
16000
16100
16200
16300
16400
16500
16600
16700
16800
16900
17000
17100
17200
17300
17400
17500
17600
17700
17800
17900
18000
18100
18200
18300
18400
1850

In [162]:
c

61104

In [181]:
k = 0
beba = [1] * n
for i in range(878):
    f = 1
    for j in range(878):
        if (G[i][j] == 0):
            beba[i] = 0
            beba[j] = 0

In [190]:
GG = [[] for _ in range(n)]
for i in range(878):
    for j in range(878):
        if (G[i][j] == 0):
            GG[i].append(j)
            GG[j].append(i)

In [198]:
c = 0
used = [0] * n
cc = 0
def ddfs(v):
    global cc
    if (used[v]):
        return;
    cc += 1
    used[v] = 1
    for u in GG[v]:
        ddfs(u)
for i in range(n):
    if (used[i] == 0):
        c += 1
        ddfs(i)
        print(c, cc)
        cc = 0

1 848
2 1
3 1
4 1
5 1
6 1
7 1
8 1
9 1
10 1
11 1
12 1
13 1
14 1
15 1
16 1
17 1
18 1
19 1
20 1
21 1
22 1
23 1
24 1
25 1
26 1
27 1
28 1
29 1
30 1
31 1


In [196]:
c

31

In [182]:
sum(beba)

30

In [178]:
N - sum(beba)

848

In [184]:
k = 30

In [168]:
k * 2000

60000

In [186]:
c

61104

In [150]:
G = J

In [151]:
(G == 1).sum()

tensor(96184)

In [152]:
(G == 0).sum()

tensor(61766)

In [153]:
graph[0]

[]

In [10]:
big = []
for i in range(n):
    if (J[i][i] >= 50):
        big.append([J[i][i], i])

In [12]:
big.sort()

In [16]:
big

[[tensor(50), 117],
 [tensor(50), 128],
 [tensor(50), 148],
 [tensor(50), 189],
 [tensor(50), 313],
 [tensor(50), 394],
 [tensor(50), 446],
 [tensor(50), 505],
 [tensor(50), 527],
 [tensor(50), 654],
 [tensor(50), 740],
 [tensor(50), 743],
 [tensor(50), 756],
 [tensor(50), 872],
 [tensor(51), 14],
 [tensor(51), 139],
 [tensor(51), 159],
 [tensor(51), 219],
 [tensor(51), 284],
 [tensor(51), 324],
 [tensor(51), 380],
 [tensor(51), 407],
 [tensor(51), 414],
 [tensor(51), 416],
 [tensor(51), 445],
 [tensor(51), 523],
 [tensor(51), 553],
 [tensor(51), 564],
 [tensor(51), 583],
 [tensor(51), 585],
 [tensor(51), 629],
 [tensor(51), 711],
 [tensor(51), 737],
 [tensor(51), 748],
 [tensor(51), 798],
 [tensor(51), 818],
 [tensor(51), 843],
 [tensor(51), 862],
 [tensor(52), 142],
 [tensor(52), 175],
 [tensor(52), 246],
 [tensor(52), 288],
 [tensor(52), 309],
 [tensor(52), 349],
 [tensor(52), 368],
 [tensor(52), 415],
 [tensor(52), 541],
 [tensor(52), 598],
 [tensor(52), 625],
 [tensor(52), 630],
 

In [15]:
len(big)

645

In [19]:
res = [[] for _ in range(n)]

In [24]:
c = 0
def greedy():
    global c, J
    imx = 0
    for i in range(n):
        if (J[imx][imx] < J[i][i]):
            imx = i
    for i in range(J[imx][imx]):
        cond = []
        for k in range(n):
            cond.append([-J[imx][k], k])
        cond.sort()
        for k in range(n):
            cond[k][0] = -cond[k][0]
        dgroup = [imx]
        for k in range(n):
            ngr = cond[k][1]
            ok = 1
            for gr in dgroup:
                if (J[ngr][gr] == 0): 
                    ok = 0
            if (ok):
                dgroup.append(ngr)
        for ii in dgroup:
            for jj in dgroup:
                J[ii][jj] -= 1
            res[ii].append(c)
        c += 1

In [25]:
J

tensor([[ 46,   5,   2,  ...,   0,   0,   0],
        [  5, 121,   8,  ...,   0,   0,   0],
        [  2,   8,  43,  ...,   0,   0,   0],
        ...,
        [  0,   0,   0,  ...,  40,   0,   0],
        [  0,   0,   0,  ...,   0,  43,   3],
        [  0,   0,   0,  ...,   0,   3,  72]])